In [2]:
import geopandas as gpd
import json
import fiona
from bokeh.io import show, output_notebook
from bokeh.models import GeoJSONDataSource, LogColorMapper
from bokeh.palettes import Magma256 as palette
from bokeh.plotting import figure,ColumnDataSource
from shapely.geometry import Polygon, Point, MultiPoint, MultiPolygon
from shapely.prepared import prep
import pandas as pd

In [3]:
#importing the packages
from bokeh.plotting import figure, show, output_file, ColumnDataSource,output_notebook
from bokeh.tile_providers import get_provider, Vendors
from bokeh.layouts import column, row, widgetbox, layout
from bokeh.models import Slider, Toggle,DateSlider,DateRangeSlider,sliders,callbacks
from bokeh.models.callbacks import CustomJS
from bokeh.models import SaveTool
from bokeh.io import curdoc,export_svgs
import pandas as pd
from geopy.geocoders import Nominatim
import numpy as np
import matplotlib.pyplot as plt
from datetime import date

In [4]:
list_of_depts = ['HPD', 'NYPD', 'DSNY', 'DOT', 'DOB', 'DPR', 'DHS']
data_dict = {}
for i in list_of_depts:
    data_dict[i] = pd.read_csv(f'./{i}_to_noah.csv')
    data_dict[i].drop(columns = 'Unnamed: 0',inplace = True)

In [ ]:
requests = pd.read_csv('./send_to_noah.csv')
requests.drop(columns='Unnamed: 0',inplace = True)

In [ ]:
requests.head()

In [5]:
shapefile = '../Community Districts/community_districts.shp'

In [6]:
geodf = gpd.read_file(shapefile)
geojson = geodf.to_json()
geodf.head()

boro_cd    shape_area    shape_leng  \
0    311.0  1.031778e+08  51549.557899   
1    313.0  8.819569e+07  65821.875617   
2    312.0  9.952550e+07  52245.830495   
3    304.0  5.666322e+07  37008.100320   
4    206.0  4.266431e+07  35875.710998   

                                            geometry  
0  POLYGON ((-73.97299433938896 40.60881414180224...  
1  POLYGON ((-73.98372152615246 40.59582107821707...  
2  POLYGON ((-73.97139631688152 40.64825778611409...  
3  POLYGON ((-73.89646625062909 40.68233642247531...  
4  POLYGON ((-73.8718461029101 40.84376077785579,...

In [7]:
shp = fiona.open(shapefile)

In [8]:
geodf['x'] = [ [x[0] for x in feat["geometry"]["coordinates"][0]] for feat in shp]
geodf['y'] = [ [y[1] for y in feat["geometry"]["coordinates"][0]] for feat in shp]

In [9]:
geodf.head()

boro_cd    shape_area    shape_leng  \
0    311.0  1.031778e+08  51549.557899   
1    313.0  8.819569e+07  65821.875617   
2    312.0  9.952550e+07  52245.830495   
3    304.0  5.666322e+07  37008.100320   
4    206.0  4.266431e+07  35875.710998   

                                            geometry  \
0  POLYGON ((-73.97299433938896 40.60881414180224...   
1  POLYGON ((-73.98372152615246 40.59582107821707...   
2  POLYGON ((-73.97139631688152 40.64825778611409...   
3  POLYGON ((-73.89646625062909 40.68233642247531...   
4  POLYGON ((-73.8718461029101 40.84376077785579,...   

                                                   x  \
0  [-73.97299433938896, -73.97258982407092, -73.9...   
1  [-73.98372152615246, -73.98304659419559, -73.9...   
2  [-73.97139631688152, -73.9712103903296, -73.97...   
3  [-73.89646625062909, -73.89652633301414, -73.8...   
4  [-73.8718461029101, -73.87191691451008, -73.87...   

                                                   y  
0  [40.60881414180224, 40.606671533373586, 40.605...  
1  [40.59582107821707, 40.59541454018628, 40.5947...  
2  [40.64825778611409, 40.647620154484, 40.646378...  
3  [40.68233642247531, 40.682002918918336, 40.681...  
4  [40.84376077785579, 40.84345374314838, 40.8432...

In [10]:
combined_df = geodf

In [11]:
combined_df = combined_df.merge(data_dict['NYPD'], left_on='boro_cd',right_on='community_board_full')

In [ ]:
for i in data_dict:
    combined_df = combined_df.merge(data_dict[i], left_on='boro_cd',right_on='community_board_full')

In [12]:
combined_df.head()

boro_cd    shape_area    shape_leng  \
0    311.0  1.031778e+08  51549.557899   
1    311.0  1.031778e+08  51549.557899   
2    311.0  1.031778e+08  51549.557899   
3    311.0  1.031778e+08  51549.557899   
4    311.0  1.031778e+08  51549.557899   

                                            geometry  \
0  POLYGON ((-73.97299433938896 40.60881414180224...   
1  POLYGON ((-73.97299433938896 40.60881414180224...   
2  POLYGON ((-73.97299433938896 40.60881414180224...   
3  POLYGON ((-73.97299433938896 40.60881414180224...   
4  POLYGON ((-73.97299433938896 40.60881414180224...   

                                                   x  \
0  [-73.97299433938896, -73.97258982407092, -73.9...   
1  [-73.97299433938896, -73.97258982407092, -73.9...   
2  [-73.97299433938896, -73.97258982407092, -73.9...   
3  [-73.97299433938896, -73.97258982407092, -73.9...   
4  [-73.97299433938896, -73.97258982407092, -73.9...   

                                                   y  Month  Year  \
0  [40.60881414180224, 40.606671533373586, 40.605...      1  2010   
1  [40.60881414180224, 40.606671533373586, 40.605...      2  2010   
2  [40.60881414180224, 40.606671533373586, 40.605...      3  2010   
3  [40.60881414180224, 40.606671533373586, 40.605...      4  2010   
4  [40.60881414180224, 40.606671533373586, 40.605...      5  2010   

   community_board_full  NYPD  
0                   311    72  
1                   311   437  
2                   311   327  
3                   311   422  
4                   311   506

In [ ]:
combined_df['Year'].min()

In [16]:
# # creating a Bokeh map
# # Break tweets dataframe into two dataframes:
all_requests = combined_df
visible_requests = combined_df[(combined_df['Year']==2010) & (combined_df['Month']==1)]

# # make column data source dictionaries for each dataset for the bokeh map

visible_source = ColumnDataSource(data = dict(x = visible_requests['x'],
                                              y = visible_requests['y'],
                                              cb = visible_requests['community_board_full'],
                                              year = visible_requests['Year'],
                                              month = visible_requests['Month'],
                                              NYPD_count = visible_requests['NYPD']
                                           )
)
all_source = ColumnDataSource(data = dict(x = all_requests['x'],
                                              y = all_requests['y'],
                                              cb = all_requests['community_board_full'],
                                              year = all_requests['Year'],
                                              month = all_requests['Month'],
                                              NYPD_count = all_requests['NYPD']
                                           )
)

#geo_source = GeoJSONDataSource(geojson=geojson)
                             

# Sidebar tools for the bokeh map
TOOLS="hover,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select"

# setting the text to display when hovering over points on map
TOOLTIPS =[
    ('CB', '@cb'),
    ('NYPD Calls', '@NYPD_count'),
    ('Year','@year'),
    ('Month','@month')
]

# callback function
# Since Bokeh renders maps using Javascript, a callback function is needed to pull in our data
# to the map app, as python code cannot be referenced in javascript
callback = CustomJS(args=dict(all_source=all_source,visible_source = visible_source), code="""
    
    var all_data = all_source.data;
    var visible_data = visible_source.data;
    var month = month.value;
    var year = year.value;
    
    visible_data.x = []
    visible_data.y = []
    visible_data.NYPD_count = []
    visible_data.cb = []
    visible_data.month = []
    visible_data.year = []
    
    for(var i =0; i < all_data.x.length; i++) {
        if ((all_data.year[i] == year)&(all_data.month[i]==month)) {
            visible_data.x.push(all_data.x[i]);
            visible_data.y.push(all_data.y[i]);
            visible_data.NYPD_count.push(all_data.NYPD_count[i]);
            visible_data.cb.push(all_data.cb[i]);
            visible_data.month.push(all_data.month[i]);
            visible_data.year.push(all_data.year[i])
        }
    }
    
    visible_source.change.emit();
""")
# Slider to control month of the year data is shown for
month_slider = Slider(start=1,end=12, value=1, step=1, title="Month", callback = callback)
callback.args['month'] = month_slider

# Slider to control year data is shown for
year_slider = Slider(start=2010, end=2019, value=2010, step=1,title="Year",callback = callback)
callback.args['year'] = year_slider

# Set Map Properties
p = figure(title='Map of 311 Requests by Community Board',plot_height = 500,tools = TOOLS, tooltips = TOOLTIPS)
# Add basemap

#p.patches('x','y',source=geo_source,fill_alpha = 0,line_color = 'grey')
p.patches('x', 'y', source=visible_source,line_color = 'grey',fill_color = {'field': 'NYPD_count','transform':LogColorMapper(palette=palette)})


layout = column(year_slider,month_slider,p)
curdoc().add_root(layout)
output_file("311_calls_map.html", title="311_calls_map.py")
output_notebook()
show(layout)  # open a browser

Loading BokehJS ...

In [ ]:
#Calculate change of population relative to 2010:
for i in range(8):
    df_states["Delta_Population_201%d"%i] = ((df_states["POPESTIMATE201%d"%i] / df_states["POPESTIMATE2010"]) -1 ) * 100

#Specify slider columns:
slider_columns = ["Delta_Population_201%d"%i for i in range(8)]

#Specify slider-range (Maps "Delta_Population_2010" -> 2010, 
#                           "Delta_Population_2011" -> 2011, ...):
slider_range = range(2010, 2018)

#Make slider plot:
df_states.plot_bokeh(
    figsize=(900, 600),
    simplify_shapes=5000,
    slider=slider_columns,
    slider_range=slider_range,
    slider_name="Year", 
    colormap="Inferno",
    hovertool_columns=["STATE_NAME"] + slider_columns,
    title="Change of Population [%]")